# 交易经验学习

## API设置

In [1]:
# -*- coding: utf-8 -*-
import concurrent
import requests
import json
import os
from retrying import retry
from tqdm import tqdm
import random
from concurrent.futures import ThreadPoolExecutor
from requests.packages.urllib3.exceptions import InsecureRequestWarning
import pandas as pd
from datetime import datetime, timedelta

import pyarrow.ipc as ipc
import pyarrow as pa
requests.packages.urllib3.disable_warnings(InsecureRequestWarning)

# openai gpt model
api_endpoint = "https://api.ai-gaochao.cn/v1"
#api_key=""
model="gpt-4o-2024-05-13"

def call_openai(api_endpoint, api_key, prompts,random_seeds, desc=""):
    url = f"{api_endpoint}/chat/completions"

    @retry(stop_max_attempt_number=5)
    def _send_post_request(url,prompt,random_seed):
        headers = {
            "Content-Type": "application/json",
            "Authorization": f"Bearer {api_key}"
        }

        payload = {
            "model": model,
            "messages": [
                {
                    'role': 'user',
                    'content': prompt
                },
            ]
        }
        # return prompt
        
        try:
            raw_response = requests.post(url, headers=headers, json=payload, verify=False)
            response_json = json.loads(raw_response.content.decode('utf-8'))

            raw_usage = response_json.get('usage', {})
            message_content = response_json.get('choices', [{}])[0].get('message', {}).get('content', '')

            response = {
                "prompt": prompt,
                "response": message_content,
                "usage": raw_usage,
                "origin_output":response_json,
                "random_seed":random_seed
            }

            tqdm.write(f"Prompt: {prompt}")
            tqdm.write(f"Response: {message_content}")
            tqdm.write(f"Usage: {raw_usage}")
        except Exception as e:
            # print(raw_response.content)
            tqdm.write(f'Error occurred: {e}. Retrying...')
            return ""
        return response

    threads = 50
    generations = []
    with tqdm(total=len(prompts), desc=desc) as pbar:
        def update(*args):
            pbar.update()
        
        with ThreadPoolExecutor(max_workers=threads) as executor:
            futures = []

            for prompt,random_seed in zip(prompts,random_seeds):
                futures.append(executor.submit(_send_post_request, url,prompt,random_seed))
            
            for future in futures:
                future.add_done_callback(update)
                
            for future in futures:
                generations.append(future.result())
    return generations


## 规定输出格式，从过去新闻中总结出交易经验

In [2]:
def extract_response_data(response):
    """
    从固定格式的字符串中提取 Summary、Keywords 和 Reason。
    """
    try:
        # 根据关键词分割字符串
        summary_part = response.split("Summary:")[1].split("Keywords:")[0].strip()
        keywords_part = response.split("Keywords:")[1].split("Reason:")[0].strip()
        reason_part = response.split("Reason:")[1].strip()

        # 将 keywords 逗号分割成列表
        keywords = [keyword.strip() for keyword in keywords_part.split(",")]

        return summary_part, keywords, reason_part
    except Exception as e:
        # 发生任何错误时，返回默认值
        print(f"Error parsing response: {e}")
        return 'N/A', [], 'N/A'
    
def read_news(file_path, excel_path, output_file):
    # 读取新闻 JSON 文件
    with open(file_path, 'r', encoding='utf-8') as file:
        news_data = json.load(file)
    
    # 读取 Excel 文件
    stock_data = pd.read_excel(excel_path)
    
    # 存储最终结果的列表
    final_results = []
    
    # 将 Date 列转换为 datetime 格式
    stock_data['Date'] = pd.to_datetime(stock_data['Date'], format='%Y-%m-%d %H:%M:%S')
    
    # 遍历新闻数据
    for article in news_data:
        title_str = f"Title: {article['title']}"
        description_str = f"Description: {article['description']}"
        published_at_str = f"Published At: {article['publishedAt']}"
        query_str = f"Query: {article['query']}"
        
        # 将新闻的发布日期转换为日期格式 (只取日期部分)
        published_date = datetime.strptime(article['publishedAt'][:10], '%Y-%m-%d').date()
        
        # 查找匹配的股价（当天）
        stock_row_today = stock_data[stock_data['Date'].dt.date == published_date]
        
        # 如果找到匹配日期的股价
        if not stock_row_today.empty:
            stock_price_today = stock_row_today.iloc[0]['Close']  # 提取当天的收盘价
            
            # 获取当前行索引
            current_index = stock_row_today.index[0]
            
            # 如果当前行不是第一行，获取上一行的收盘价
            if current_index > 0:
                stock_price_yesterday = stock_data.iloc[current_index - 1]['Close']
                
                # 比较当天和上一行的股价
                if stock_price_today > stock_price_yesterday:
                    stock_change_str = f"The stock is up today and the share price is {stock_price_today:.2f}"
                elif stock_price_today < stock_price_yesterday:
                    stock_change_str = f"The stock is down today and the share price is {stock_price_today:.2f}"
                else:
                    stock_change_str = f"The stock is flat  today and the share price is {stock_price_today:.2f}"
            else:
                stock_change_str = f"Today's share price is {stock_price_today:.2f}（No previous day's data for comparison）"
        else:
            stock_change_str = "Day is not a trading day, there is no stock price for that day"
        
        # 打印结果
        print(title_str)
        print(description_str)
        print(published_at_str)
        print(query_str)
        print(stock_change_str)
        print("-" * 40)  # 分隔线
        # 生成最终总结的prompt
        prompt = f"""
        You are a stock analyst and very good at summarizing why stocks go up and down. I'll give you the news and the ups and downs about Apple today.
        You need to accomplish 3 things: 1. summarize the news about this article and write a news summary. 2. summarize the keywords of the news to make it easier for me to retrieve the event in the future. 3. reason out the causes based on the rise and fall of the stock price today. If today is not a trading day, the stock price did not fluctuate, just analyze the impact on the stock price.
        Here is the news:{title_str}{description_str}
        Here is the ups and downs:{stock_change_str}
        Your output has to be in formatted as below:
        Summary: Today, there is growing excitement around a concept video showcasing a potential foldable iPhone, referred to as the iPhone Flip. Speculation about Apple's foray into foldable smartphone technology has been circulating, and the video has sparked considerable interest among enthusiasts and investors alike. The allure of innovative product development and Apple's continuous push for cutting-edge technology is capturing the market's attention.
        Keywords: iPhone Flip, foldable iPhone concept, Apple innovation, iPhone 13 comparison, future Apple products
        Reason: The stock price of Apple increased today, reaching $152.51, largely due to the positive sentiment and hype generated by the iPhone Flip concept video. Investors are optimistic about Apple's potential entry into the foldable smartphone market, which could introduce a significant new revenue stream and further solidify Apple's market position as a leader in technological innovation. This excitement over future product possibilities is driving up the stock price.
        """
        # 调用函数生成最终总结
        generations = call_openai(api_endpoint, api_key, [prompt], [42], desc="Generating Final Summary")
        summary_string = generations[0]['response']
        summary, keywords, reason = extract_response_data(summary_string)
        # 将新闻和分析结果存储在一起
        result = {
            'title': article['title'],
            'description': article['description'],
            'publishedAt': article['publishedAt'],
            'query': article['query'],
            'stock_change': stock_change_str,
            'Summary': summary,
            'Query': keywords,
            'Reason': reason
        }
        
        # 将结果添加到最终列表中
        final_results.append(result)
            # 将最终结果写入新的 JSON 文件
    with open(output_file, 'w', encoding='utf-8') as outfile:
        json.dump(final_results, outfile, ensure_ascii=False, indent=4)
        

# 使用示例
read_news('APPLE.json', 'APPLE.xlsx', 'APPLE_EXP.json')

Title: NJ suburb turned into transit hub where migrants switch from buses to trains to thwart NYC crackdown
Description: Buses of migrant families are thwarting Eric Adam's crackdown on arrivals in the Big Apple by switching to trains in a New Jersey suburb and traveling to their "final destination" in New York City.
Published At: 2024-01-01T23:03:55Z
Query: APPLE
Day is not a trading day, there is no stock price for that day
----------------------------------------


Generating Final Summary: 100%|██████████| 1/1 [00:02<00:00,  2.90s/it]


Prompt: 
        You are a stock analyst and very good at summarizing why stocks go up and down. I'll give you the news and the ups and downs about Apple today.
        You need to accomplish 3 things: 1. summarize the news about this article and write a news summary. 2. summarize the keywords of the news to make it easier for me to retrieve the event in the future. 3. reason out the causes based on the rise and fall of the stock price today. If today is not a trading day, the stock price did not fluctuate, just analyze the impact on the stock price.
        Here is the news:Title: NJ suburb turned into transit hub where migrants switch from buses to trains to thwart NYC crackdownDescription: Buses of migrant families are thwarting Eric Adam's crackdown on arrivals in the Big Apple by switching to trains in a New Jersey suburb and traveling to their "final destination" in New York City.
        Here is the ups and downs:Day is not a trading day, there is no stock price for that day
   

Generating Final Summary: 100%|██████████| 1/1 [00:04<00:00,  4.03s/it]


Prompt: 
        You are a stock analyst and very good at summarizing why stocks go up and down. I'll give you the news and the ups and downs about Apple today.
        You need to accomplish 3 things: 1. summarize the news about this article and write a news summary. 2. summarize the keywords of the news to make it easier for me to retrieve the event in the future. 3. reason out the causes based on the rise and fall of the stock price today. If today is not a trading day, the stock price did not fluctuate, just analyze the impact on the stock price.
        Here is the news:Title: Apple Watch Controversy: Masimo's CEO Speaks OutDescription: Learn why Masimo's CEO refuses to back down in the ongoing lawsuit against Apple. Explore the patent dispute and its potential consequences
        Here is the ups and downs:Day is not a trading day, there is no stock price for that day
        Your output has to be in formatted as below:
        Summary: Today, there is growing excitement around a

...

Prompt: 
        You are a stock analyst and very good at summarizing why stocks go up and down. I'll give you the news and the ups and downs about Apple today.
        You need to accomplish 3 things: 1. summarize the news about this article and write a news summary. 2. summarize the keywords of the news to make it easier for me to retrieve the event in the future. 3. reason out the causes based on the rise and fall of the stock price today. If today is not a trading day, the stock price did not fluctuate, just analyze the impact on the stock price.
        Here is the news:Title: Martinelli's recalls apple juice sold at Target, Whole Foods over high arsenic levelsDescription: Martinelli's recalled one lot of its beloved apple juice being sold at major retailers across the US including Target, Whole Foods and Publix over high levels of inorganic arsenic.
        Here is the ups and downs:The stock is down today and the share price is 170.33
        Your output has to be in formatted a

Generating Final Summary: 100%|██████████| 1/1 [00:02<00:00,  2.62s/it]


Prompt: 
        You are a stock analyst and very good at summarizing why stocks go up and down. I'll give you the news and the ups and downs about Apple today.
        You need to accomplish 3 things: 1. summarize the news about this article and write a news summary. 2. summarize the keywords of the news to make it easier for me to retrieve the event in the future. 3. reason out the causes based on the rise and fall of the stock price today. If today is not a trading day, the stock price did not fluctuate, just analyze the impact on the stock price.
        Here is the news:Title: Apple confirms bug that is keeping some iPhone alarms from soundingDescription: If your iPhone hasn't been waking you up lately, you're not alone.
        Here is the ups and downs:The stock is down today and the share price is 170.33
        Your output has to be in formatted as below:
        Summary: Today, there is growing excitement around a concept video showcasing a potential foldable iPhone, referred

Generating Final Summary: 100%|██████████| 1/1 [00:06<00:00,  6.02s/it]

Prompt: 
        You are a stock analyst and very good at summarizing why stocks go up and down. I'll give you the news and the ups and downs about Apple today.
        You need to accomplish 3 things: 1. summarize the news about this article and write a news summary. 2. summarize the keywords of the news to make it easier for me to retrieve the event in the future. 3. reason out the causes based on the rise and fall of the stock price today. If today is not a trading day, the stock price did not fluctuate, just analyze the impact on the stock price.
        Here is the news:Title: Dark Matter Producers On The "Fascinating Process" Of Developing Apple TV+'s Multiverse ShowDescription: Dark Matter EPs Blake Crouch & Matt Tolmach discuss exploring the multiverse, the casting process, and expanding the story beyond the novel.
        Here is the ups and downs:The stock is down today and the share price is 170.33
        Your output has to be in formatted as below:
        Summary: Today, 